In [36]:
import pandas as pd
import math
from datetime import datetime
import hvplot.pandas
import math
import numpy as np
# load data
profile_df = pd.read_pickle('../data/portfolio_portfile.pkl')
benchmark_df = pd.read_pickle('../data/benchmark_portfolio.pkl')
portfolio_df = pd.read_pickle('../data/portfolio_data.pkl')

## This section transfrom benchmark_df and creat an benchmark profile to accomadate current pipeline

In [37]:
# drop weight
# benchmark_df = benchmark_df.drop(columns=['weight'])

## simulate update potfolio weigth at 2021-01-10
update_profile_df = profile_df.copy()
update_profile_df['date'] = datetime(2021,1,10)
update_profile_df['weight'] = [50,100,200,300,400,500]
profile_df = pd.concat([profile_df, update_profile_df])


In [38]:
## create a profile for benchmark
b_profile = benchmark_df.drop_duplicates(subset=['ticker', 'actual_data'])
# df_unique[df_unique.ticker == "000008.XSHE"]
# only keep ticker	date	weight	display_name	name	sector	aggregate_sector column
b_profile = b_profile[['ticker','date','weight','name','sector','aggregate_sector','display_name_x']]
b_profile.rename(columns={'display_name_x': 'display_name'}, inplace=True)

In [39]:
# drop weight in benchmark
benchmark_df = benchmark_df.drop(columns=['weight'])
benchmark_df = benchmark_df.drop(columns=['display_name_x'])
# drop display_name_y
benchmark_df = benchmark_df.drop(columns=['display_name_y'])
# drop actual_data
benchmark_df = benchmark_df.drop(columns=['actual_data'])
# drop name
benchmark_df = benchmark_df.drop(columns=['name'])
# drop aggregate_sector
benchmark_df = benchmark_df.drop(columns=['aggregate_sector'])
# drop sector
benchmark_df = benchmark_df.drop(columns=['sector'])
benchmark_df.head(1)

date       ticker  open  close  high   low      volume        money
0 2021-01-05  000008.XSHE  2.52   2.57  2.67  2.49  33215803.0  85358605.99

In [40]:
for col_name in benchmark_df.columns:
    if (col_name not in portfolio_df.columns):
        print(f'portfolio does not have {col_name}')
    

for col_name in portfolio_df.columns:
    if (col_name not in benchmark_df.columns):
        print(f'benchmark does not have {col_name}')

In [41]:
for col_name in b_profile.columns:
    print(col_name in profile_df.columns)

for col_name in profile_df.columns:
    print(col_name in b_profile.columns)

True
True
True
True
True
True
True
True
True
True
True
True
True
True


## calculate result for each individual stock this part should return a table

In [42]:
def get_processing_result_of_stocks_df(stock_df, profile_df):
    ## add sector_name display_name name
    ticker_sector_map = dict(zip(profile_df['ticker'], profile_df['aggregate_sector']))
    ticker_display_name_map = dict(zip(profile_df['ticker'], profile_df['display_name']))
    ticker_name_map = dict(zip(profile_df['ticker'], profile_df['name']))

    stock_df['display_name'] = stock_df['ticker'].map(ticker_display_name_map)
    stock_df['name'] = stock_df['ticker'].map(ticker_name_map)
    stock_df['aggregate_sector'] = stock_df['ticker'].map(ticker_sector_map)

    ## calculate pct using closing price
    stock_df.sort_values(by=['date'], inplace=True)
    stock_df['pct'] = stock_df.groupby('ticker')['close'].pct_change()

    ## calculate weight TODO: think about how to optimize this
    stock_df = stock_df.merge(profile_df[['weight', 'date', 'ticker']], on=['ticker', 'date'], how='outer')
    stock_df.rename(columns={'weight': 'initial_weight'}, inplace=True)
    stock_df['current_weight'] = float('nan')
    stock_df['previous_weight'] = float('nan')
    df_grouped = stock_df.groupby('ticker')
    for _, group in df_grouped:
        pre_w = float('nan')
        ini_w = float('nan')
        for index, row in group.iterrows():
            cur_w = float('nan')

            # if has initial weight, the following row all use this initial weight
            if not pd.isna(row['initial_weight']):
                ini_w = row['initial_weight']
                cur_w = ini_w

            # just calculate current weight based on previous weight
            else:
                cur_w = pre_w * (1 + row['pct'])

            stock_df.loc[index, 'current_weight'] = cur_w    
            stock_df.loc[index, 'previous_weight'] = pre_w
            stock_df.loc[index, 'initial_weight'] = ini_w
            pre_w = cur_w

    stock_df.rename(columns={'weight': 'initial_weight'}, inplace=True)
    stock_df.dropna(subset=['close'], inplace=True)

    ## normalize weight
    stock_df['prev_w_in_p'] = stock_df['previous_weight'] / \
                                    stock_df.groupby('date')['previous_weight'].transform('sum')

    stock_df['ini_w_in_p'] = stock_df['initial_weight'] / \
                                    stock_df.groupby('date')['initial_weight'].transform('sum')

    ## calculate weighted pct in portfolio
    stock_df['portfolio_pct'] = stock_df['pct'] * stock_df['prev_w_in_p']

    ## calculate weight in sector TODO: remove
    stock_df['prev_w_in_sectore'] = stock_df['previous_weight'] / \
                                                stock_df.groupby(['date', 'aggregate_sector'])['previous_weight'].transform('sum')
    stock_df['ini_w_in_sector'] = stock_df['initial_weight'] / \
                                                stock_df.groupby(['date', 'aggregate_sector'])['initial_weight'].transform('sum')
    ## weighted pct in sector TODO: remove
    stock_df['sector_pct'] = stock_df['pct'] * stock_df['prev_w_in_sectore']

    ## portfolio return
    stock_df['cum_p_pct'] = stock_df.groupby('ticker')['portfolio_pct'].cumsum()
    stock_df['portfolio_return'] = np.exp(stock_df['cum_p_pct']) -1 
    # drop intermediate columns
    stock_df = stock_df.drop(columns=['cum_p_pct'])


    ## sector return TODO:remove 
    # stock_df['sector_return'] = stock_df['ini_w_in_sector'] * stock_df['return']

    return stock_df


In [43]:
# portfolio_stock = get_processing_result_of_stocks_df(portfolio_df, profile_df)
# portfolio_stock[portfolio_stock.ticker == '002709.XSHE'][['date','portfolio_pct','prev_w_in_p','portfolio_return']]
# # benchmark_stock = get_processing_result_of_stocks_df(benchmark_df, b_profile)

In [44]:
# profile_df.groupby('date')['weight'].sum()

In [45]:
## total return by date
def get_portfolio_evaluation(portfolio_stock, benchmark_stock, profile_df):
    # add pct of benchmark 
    merged_df = portfolio_stock.merge(benchmark_stock[['ticker','date','portfolio_pct','portfolio_return']], 
                                    on=['ticker','date'],how='left',suffixes=('_p','_b'))

    # sum up pct and return from portfolio and benchmark
    merged_df = merged_df.groupby('date',as_index=False).agg({'portfolio_return_p':'sum',
                                                            'portfolio_return_b':'sum',
                                                            'portfolio_pct_p':'sum',
                                                            'portfolio_pct_b':'sum'})

    # portfolio mkt cap
    mkt_adjustment = pd.DataFrame(profile_df.groupby('date')['weight'].sum())
    mkt_adjustment.rename(columns={'weight':'mkt_cap'}, inplace=True)
    merged_df = merged_df.merge(mkt_adjustment, on=['date'], how='outer')

    for i in range(len(merged_df)):
        if pd.isna(merged_df.loc[i, 'mkt_cap']):
            merged_df.loc[i, 'mkt_cap'] = merged_df.loc[i-1, 'mkt_cap'] * (1 + merged_df.loc[i, 'portfolio_pct_p'])
    # drop where portfolio_return_p is nan
    merged_df.dropna(subset=['portfolio_return_p'], inplace=True)
    # portfolio pnl TODO seem I can just use current wegith to do this
    merged_df['prev_mkt_cap'] = merged_df['mkt_cap'].shift(1)
    merged_df['pnl'] = merged_df['prev_mkt_cap'] * merged_df['portfolio_pct_p']

    # risk std(pct)
    merged_df['risk'] = merged_df['portfolio_pct_p'].rolling(len(merged_df), min_periods=1).std() * math.sqrt(252)

    # active return
    merged_df['active_return'] = merged_df['portfolio_pct_p'] - merged_df['portfolio_pct_b']

    # tracking errro std(active return)
    merged_df['tracking_error'] = merged_df['active_return'].rolling(len(merged_df), min_periods=1).std() * math.sqrt(252)

    # cum pnl
    merged_df['cum_pnl'] = merged_df['pnl'].cumsum()

    return merged_df


In [46]:
# portfolio_eval_df = get_portfolio_evaluation(portfolio_stock, benchmark_stock, profile_df)

In [47]:
# portfolio_stock.columns

In [48]:
## TODO convert below to funciton

def get_portfolio_sector_evaluation(portfolio_stock,benchmark_df):
# aggregate on sector and day
    p_sector_df = portfolio_stock.groupby(['date','aggregate_sector'], as_index=False)\
        .agg({'prev_w_in_p': 'sum','ini_w_in_p':"sum","current_weight":'sum',\
            "portfolio_pct":"sum", "portfolio_return":"sum"})
    # TODO shrink it down before aggregate
    b_sector_df = benchmark_df.groupby(['date','aggregate_sector'], as_index=False)\
        .agg({'prev_w_in_p': 'sum','ini_w_in_p':"sum","current_weight":'sum',\
            "portfolio_pct":"sum", "portfolio_return":"sum"})
    
    # merge portfolio and benchmark
    merge_df = p_sector_df.merge(b_sector_df, on=['date','aggregate_sector'], how='left', suffixes=('_p','_b'))

    return merge_df

In [49]:
# sector_eval_df = get_portfolio_sector_evaluation(portfolio_stock, benchmark_stock)
# sector_eval_df[sector_eval_df.date == datetime(2021, 10,13)].hvplot.bar(x='aggregate_sector', y=['portfolio_pct_p','portfolio_pct_b'], stacked=True, rot=90, title='sector pct')

In [50]:
def merge_on_date(portfolio_stock, benchmark_df):
    p_selected = portfolio_stock.reset_index()[['ini_w_in_p', 'portfolio_return', 'date', 'ticker', 'display_name']]
    b_selected = benchmark_df.reset_index()[['ini_w_in_p', 'portfolio_return', 'date', 'ticker']]
    merged_stock_df = pd.merge(p_selected, b_selected, on=['date', 'ticker'], how='outer', suffixes=('_p', '_b'))
    return merged_stock_df

In [51]:
# merged_df = merge_on_date(portfolio_stock, benchmark_stock)

In [52]:
def get_bhb_result(merged_stock_df):
    # merged_stock_df['ini_w_in_p_p'].fillna(0, inplace=True)
    # merged_stock_df['ini_w_in_p_b'].fillna(0, inplace=True)
    # merged_stock_df['portfolio_return_b'].fillna(0, inplace=True)
    # merged_stock_df['portfolio_return_p'].fillna(0, inplace=True)
    # allocation
    merged_stock_df['allocation'] = (merged_stock_df['ini_w_in_p_p'] - merged_stock_df['ini_w_in_p_b']) \
        * merged_stock_df['portfolio_return_b']

    # selection
    merged_stock_df['selection'] = merged_stock_df['ini_w_in_p_b'] * \
        (merged_stock_df['portfolio_return_p'] - merged_stock_df['portfolio_return_b'])

    # interaction
    merged_stock_df['interaction'] = (merged_stock_df['ini_w_in_p_p'] - merged_stock_df['ini_w_in_p_b']) * \
        (merged_stock_df['portfolio_return_p'] - merged_stock_df['portfolio_return_b'])

    # excess
    merged_stock_df['excess'] = merged_stock_df['portfolio_return_p'] - merged_stock_df['portfolio_return_b']

    # replace inf with nan
    merged_stock_df.replace([np.inf, -np.inf], np.nan, inplace=True)
    return merged_stock_df

In [53]:
# test ing pipeline here 

In [54]:
portfolio_stock = get_processing_result_of_stocks_df(portfolio_df, profile_df)
benchmark_stock = get_processing_result_of_stocks_df(benchmark_df, b_profile)

portfolio_eval_df = get_portfolio_evaluation(portfolio_stock, benchmark_stock, profile_df)
sector_eval_df = get_portfolio_sector_evaluation(portfolio_stock, benchmark_stock)
merged_df = merge_on_date(portfolio_stock, benchmark_stock)
bnb_sector_result = get_bhb_result(sector_eval_df)
bnb_stock_result = get_bhb_result(merged_df)


In [ ]:
# save result 
portfolio_eval_df.to_pickle('../data/portfolio_eval_df.pkl')
sector_eval_df.to_pickle('../data/sector_eval_df.pkl')
# merged_df.to_csv('merged_df.csv')
bnb_sector_result.to_pickle('../data/bnb_sector_result.pkl')
bnb_stock_result.to_pickle('../data/bnb_stock_result.pkl')
profile_df.to_pickle('../data/protfolio_profile.pkl')
b_profile.to_pickle('../data/benchmark_profile.pkl')

In [ ]:
# bnb_sector_result[bnb_sector_result.date == datetime(2021, 10,13)].hvplot.bar(x='aggregate_sector', y=['allocation','selection','interaction'], stacked=True, rot=90, title='sector allocation')